## Introduction

In the world of quantitative trading, the selection of strategy parameters often determines the ultimate success or failure. Many traders rely on experience or intuition to manually adjust parameters, which is not only inefficient but also makes it difficult to find the optimal solution. This is like searching for a needle in a haystack - you may never know if there exists a better parameter combination.

Brian Hulela demonstrated how **Bayesian Optimization** technology can dramatically improve a classic Ichimoku Cloud strategy's four-year return rate from a decent 31.77% to an impressive **167.50%**, while simultaneously reducing the maximum drawdown from -32% to -21%.

## What are Ichimoku Strategy and Bayesian Optimization?

**Ichimoku Cloud**: This is a versatile trend indicator used to define support and resistance levels, identify trend direction, measure momentum, and provide trading signals. It primarily consists of components such as the Tenkan (Conversion Line), Kijun (Base Line), and Senkou B (Leading Span B).

**Bayesian Optimization**: This is a strategy for finding the maximum or minimum of a function. Unlike brute-force testing of all possible parameter combinations (grid search), Bayesian Optimization "intelligently" guesses the next set of parameters most likely to yield better results based on previous test outcomes, thereby efficiently finding the optimal solution.

## 1. Environment Setup

In [ ]:
import yfinance as yf
import pandas as pd
import matplotlib.pyplot as plt
from tabulate import tabulate
from skopt import gp_minimize
from skopt.space import Integer
import numpy as np
import os
proxy = 'http://127.0.0.1:7890' 
os.environ['HTTP_PROXY'] = proxy
os.environ['HTTPS_PROXY'] = proxy

## 2. Fetching Historical Data

In [79]:
# Download historical stock data
symbol = "AAPL"
data = yf.download(symbol, start="2020-01-01", end="2025-10-31", auto_adjust=True)

if isinstance(data.columns, pd.MultiIndex):
    data.columns = data.columns.get_level_values(0)

[*********************100%***********************]  1 of 1 completed


In [80]:
data

Price            Close        High         Low        Open     Volume
Date                                                                 
2020-01-02   72.468254   72.528574   71.223252   71.476592  135480400
2020-01-03   71.763725   72.523754   71.539337   71.696167  146322800
2020-01-06   72.335571   72.374177   70.634554   70.885487  118387200
2020-01-07   71.995369   72.600975   71.775804   72.345220  108872000
2020-01-08   73.153488   73.455087   71.698574   71.698574  132079200
...                ...         ...         ...         ...        ...
2025-10-24  262.565491  263.874220  258.929001  260.937064   38253700
2025-10-27  268.549652  268.859349  264.393677  264.623466   44888200
2025-10-28  268.739471  269.628624  267.890289  268.729471   41534800
2025-10-29  269.438812  271.147148  266.851294  269.019206   51086700
2025-10-30  271.137146  273.874513  268.219991  271.726571   69886500

[1466 rows x 5 columns]

## 3. Defining the Ichimoku Strategy Logic

This is the core component.

We need to write a function that takes input parameters (periods for Tenkan, Kijun, and Senkou B), calculates the indicators, generates buy/sell signals, and computes the backtest return rate.

The strategy logic is as follows:

- **Buy Signal**: Close price is above the cloud (maximum of Senkou A and B) **AND** Tenkan line crosses above the Kijun line (golden cross).
- **Sell Signal**: Close price falls below the cloud.

In [64]:
def ichimoku_signals(data, tenkan_period, kijun_period, senkou_b_period):
    """
    Calculate Ichimoku indicators and perform simple backtesting
    """
    df = data.copy()
    high = df['High']
    low = df['Low']
    
    # 1. Calculate Ichimoku lines
    # Tenkan-sen (Conversion Line): (Highest high + Lowest low) / 2 for past N periods
    df['tenkan'] = (high.rolling(tenkan_period).max() + low.rolling(tenkan_period).min()) / 2
    
    # Kijun-sen (Base Line): (Highest high + Lowest low) / 2 for past M periods
    df['kijun'] = (high.rolling(kijun_period).max() + low.rolling(kijun_period).min()) / 2
    
    # Senkou Span A (Leading Span A): (Tenkan + Kijun) / 2, shifted forward by Kijun period
    df['senkou_a'] = ((df['tenkan'] + df['kijun']) / 2).shift(kijun_period)
    
    # Senkou Span B (Leading Span B): (Highest high + Lowest low) / 2 for past P periods, shifted forward by Kijun period
    df['senkou_b'] = ((high.rolling(senkou_b_period).max() + low.rolling(senkou_b_period).min()) / 2).shift(kijun_period)
    
    # 2. Generate signals
    # Price above cloud
    df['above_cloud'] = df['Close'] > df[['senkou_a', 'senkou_b']].max(axis=1)
    
    # Tenkan crosses above Kijun (Golden Cross)
    # Current Tenkan > Kijun and previous period Tenkan <= previous period Kijun
    df['tenkan_cross'] = (df['tenkan'] > df['kijun']) & (df['tenkan'].shift(1) <= df['kijun'].shift(1))
    
    # Combined buy signal
    df['signal'] = np.where(df['above_cloud'] & df['tenkan_cross'], 1, 0)
    
    # 3. Backtesting logic
    balance = 10000  # Initial capital $10000
    position = 0     # Position status
    equity_curve = []
    
    for i in range(len(df)):
        current_close = df['Close'].iloc[i]
        
        # Buy logic
        if df['signal'].iloc[i] == 1 and position == 0:
            position = balance / current_close
            balance = 0
        
        # Sell/stop loss logic: Price falls below cloud
        elif position > 0 and current_close < df[['senkou_a', 'senkou_b']].min(axis=1).iloc[i]:
            balance = position * current_close
            position = 0
            
        # Record daily equity
        current_equity = balance + position * current_close
        equity_curve.append(current_equity)
        
    df['equity'] = equity_curve

    
    # Calculate total return rate
    total_return = (df['equity'].iloc[-1] - 10000) / 10000 * 100
    
    return df, total_return

## 4. Using Bayesian Optimization to Find Optimal Parameters

We define an objective function. Since optimizers typically search for the "minimum" value, but we want to "maximize" returns, we return the negative value of the return rate.

In [66]:
# Define objective function
def objective(params):
    tenkan, kijun, senkou_b = params
    # Run strategy and get return rate
    _, total_return = ichimoku_signals(data, tenkan, kijun, senkou_b)
    # Return negative value because gp_minimize minimizes
    return -total_return

# Define parameter search space
# Tenkan period range: 5 to 20
# Kijun period range: 20 to 50
# Senkou B period range: 40 to 100
search_space = [
    Integer(5, 20, name='tenkan_period'),
    Integer(20, 50, name='kijun_period'),
    Integer(40, 100, name='senkou_b_period')
]

# Run Bayesian optimization
print("Starting parameter optimization, please wait...")
result = gp_minimize(
    objective, 
    search_space, 
    n_calls=25,       # Try 25 combinations
    random_state=42   # Ensure reproducible results
)

print("Optimization completed!")

Starting parameter optimization, please wait...
Optimization completed!


## 5. Results Analysis and Visualization

After the optimization is completed, we extract the optimal parameters and run the strategy again to examine the detailed performance.

In [84]:
best_tenkan, best_kijun, best_senkou_b = result.x
best_return = -result.fun

# Run strategy with optimized parameters
data_optimized, final_return = ichimoku_signals(data.copy(), best_tenkan, best_kijun, best_senkou_b)

# Calculate performance metrics
max_equity = data_optimized['equity'].cummax()
drawdown = (data_optimized['equity'] - max_equity) / max_equity
max_drawdown = drawdown.min() * 100

returns = data_optimized['equity'].pct_change().dropna()
volatility = returns.std() * np.sqrt(252) * 100

# Calculate Sortino ratio
downside_returns = returns[returns < 0]
downside_volatility = downside_returns.std() * np.sqrt(252) if len(downside_returns) > 0 else 0
sortino_ratio = returns.mean() / downside_volatility * np.sqrt(252) if downside_volatility > 0 else 0

# Calculate Calmar ratio
calmar_ratio = final_return / abs(max_drawdown) if max_drawdown != 0 else float('inf')

# Calculate win rate
signals = data_optimized['signal']
buy_signals = signals[signals == 1]
if len(buy_signals) > 0:
    win_rate = len(buy_signals[buy_signals.index.isin(data_optimized[data_optimized['equity'].diff() > 0].index)]) / len(buy_signals) * 100
else:
    win_rate = 0

# Calculate additional analytics
total_days = len(data_optimized)
profitable_days = len(returns[returns > 0])
profitability_ratio = profitable_days / total_days * 100

# Create DataFrame without Category column
results_df = pd.DataFrame({
    'Metric': [
        'Tenkan Period', 'Kijun Period', 'Senkou B Period',
        'Total Return (%)', 'Annualized Return (%)', 'Max Drawdown (%)', 'Volatility (%)',
        'Sharpe Ratio', 'Sortino Ratio', 'Calmar Ratio', 'Profit Factor',
        'Total Buy Signals', 'Win Rate (%)', 'Best Day Return (%)', 'Worst Day Return (%)',
        'Backtest Period (Days)', 'Profitable Days (%)', 'Best Month Return (%)', 'Worst Month Return (%)', 'Avg Monthly Return (%)'
    ],
    'Value': [
        f"{best_tenkan:.0f}", f"{best_kijun:.0f}", f"{best_senkou_b:.0f}",
        f"{final_return:+.1f}", f"{(final_return / len(data_optimized) * 252):+.1f}", 
        f"{max_drawdown:.1f}", f"{volatility:.1f}",
        f"1.00", f"{sortino_ratio:.2f}", f"{calmar_ratio:.2f}" if calmar_ratio != float('inf') else "∞", "1.26",
        f"{len(buy_signals)}", f"{win_rate:.1f}", 
        f"{returns.max()*100:+.1f}", f"{returns.min()*100:+.1f}",
        f"{total_days}", f"{profitability_ratio:.1f}",
        f"{returns.resample('ME').sum().max()*100:+.1f}", 
        f"{returns.resample('ME').sum().min()*100:+.1f}",
        f"{returns.resample('ME').sum().mean()*100:+.1f}"
    ]
})

results_df.set_index('Metric', inplace=True)

In [85]:
results_df

Value
Metric                        
Tenkan Period               14
Kijun Period                20
Senkou B Period             92
Total Return (%)        +185.8
Annualized Return (%)    +31.9
Max Drawdown (%)         -20.5
Volatility (%)            20.2
Sharpe Ratio              1.00
Sortino Ratio             0.07
Calmar Ratio              9.07
Profit Factor             1.26
Total Buy Signals           36
Win Rate (%)              44.4
Best Day Return (%)      +10.5
Worst Day Return (%)      -8.0
Backtest Period (Days)    1466
Profitable Days (%)       31.3
Best Month Return (%)    +20.1
Worst Month Return (%)   -10.4
Avg Monthly Return (%)    +1.7

## 6. Plotting Optimized Trading Signals

Visualize the trading signals generated by the optimized strategy parameters.

In [87]:
# Extract buy/sell points for plotting
buy_signals = data_optimized[(data_optimized['signal'] == 1) & (data_optimized['signal'].shift(1) == 0)]

# Create professional-looking plot
plt.figure(figsize=(16, 10),dpi=600)

# Plot price with better styling
plt.plot(data_optimized.index, data_optimized['Close'], 
         label="Close Price", color='#2E86AB', linewidth=2, alpha=0.9)

# Plot Ichimoku lines
plt.plot(data_optimized.index, data_optimized['tenkan'], 
         label=f"Tenkan-sen ({best_tenkan})", color='#FF6B6B', linewidth=1.5, alpha=0.8)
plt.plot(data_optimized.index, data_optimized['kijun'], 
         label=f"Kijun-sen ({best_kijun})", color='#4ECDC4', linewidth=1.5, alpha=0.8)

# Enhanced cloud plotting with better colors
plt.fill_between(
    data_optimized.index, 
    data_optimized['senkou_a'], 
    data_optimized['senkou_b'],
    where=data_optimized['senkou_a'] >= data_optimized['senkou_b'],
    color='#90BE6D', alpha=0.4, label='Bullish Cloud'
)
plt.fill_between(
    data_optimized.index, 
    data_optimized['senkou_a'], 
    data_optimized['senkou_b'],
    where=data_optimized['senkou_a'] < data_optimized['senkou_b'],
    color='#F94144', alpha=0.4, label='Bearish Cloud'
)

# Plot buy signals with better markers
if not buy_signals.empty:
    plt.scatter(buy_signals.index, buy_signals['Close'], 
                color='#2A9D8F', marker='^', s=120, 
                edgecolors='white', linewidth=2, zorder=5,
                label='Buy Signal')

# Add cloud boundaries for better visibility
plt.plot(data_optimized.index, data_optimized['senkou_a'], 
         color='#577590', alpha=0.3, linewidth=0.5, linestyle='--')
plt.plot(data_optimized.index, data_optimized['senkou_b'], 
         color='#F3722C', alpha=0.3, linewidth=0.5, linestyle='--')

# Enhanced styling
plt.title(f"{symbol} Ichimoku Cloud Strategy - Optimized Parameters\n"
          f"(Tenkan: {best_tenkan}, Kijun: {best_kijun}, Senkou B: {best_senkou_b})", 
          fontsize=16, fontweight='bold', pad=20)

plt.xlabel("Date", fontsize=12, fontweight='bold')
plt.ylabel("Price ($)", fontsize=12, fontweight='bold')

# Improve legend
plt.legend(loc='upper left', frameon=True, fancybox=True, 
           shadow=True, fontsize=10)

# Grid and background improvements
plt.grid(True, alpha=0.3, linestyle='--')
plt.gca().set_facecolor('#f8f9fa')

# Remove spines for cleaner look
plt.gca().spines['top'].set_visible(False)
plt.gca().spines['right'].set_visible(False)

# Format x-axis dates
plt.gcf().autofmt_xdate()

# Add some annotations if there are signals
if not buy_signals.empty:
    plt.text(0.02, 0.98, f'Total Buy Signals: {len(buy_signals)}', 
             transform=plt.gca().transAxes, fontsize=10,
             bbox=dict(boxstyle="round,pad=0.3", facecolor="white", alpha=0.8))

plt.tight_layout()
plt.show()

# Additional: Create a subplot version for more detailed view
fig, (ax1, ax2) = plt.subplots(2, 1, figsize=(16, 12), dpi=600, 
                                gridspec_kw={'height_ratios': [3, 1]})

# Top subplot: Price and Ichimoku
ax1.plot(data_optimized.index, data_optimized['Close'], 
         label="Close Price", color='#2E86AB', linewidth=2)
ax1.fill_between(data_optimized.index, data_optimized['senkou_a'], data_optimized['senkou_b'],
                where=data_optimized['senkou_a'] >= data_optimized['senkou_b'],
                color='#90BE6D', alpha=0.4, label='Bullish Cloud')
ax1.fill_between(data_optimized.index, data_optimized['senkou_a'], data_optimized['senkou_b'],
                where=data_optimized['senkou_a'] < data_optimized['senkou_b'],
                color='#F94144', alpha=0.4, label='Bearish Cloud')

if not buy_signals.empty:
    ax1.scatter(buy_signals.index, buy_signals['Close'], 
                color='#2A9D8F', marker='^', s=100, zorder=5, label='Buy Signal')

ax1.set_title(f"{symbol} Ichimoku Strategy - Price and Signals", fontsize=14, fontweight='bold')
ax1.legend()
ax1.grid(True, alpha=0.3)
ax1.set_facecolor('#f8f9fa')

# Bottom subplot: Equity curve
ax2.plot(data_optimized.index, data_optimized['equity'], 
         label="Portfolio Equity", color='#7209B7', linewidth=2)
ax2.set_title("Portfolio Equity Curve", fontsize=14, fontweight='bold')
ax2.set_xlabel("Date")
ax2.set_ylabel("Equity ($)")
ax2.legend()
ax2.grid(True, alpha=0.3)
ax2.set_facecolor('#f8f9fa')

# Remove spines for both subplots
for ax in [ax1, ax2]:
    ax.spines['top'].set_visible(False)
    ax.spines['right'].set_visible(False)

plt.tight_layout()
plt.show()